# Starting a gym/recreation area in Metro Manila

## Introduction

The Philippines is an island country in South-East Asia with a population of more than 100 million [https://www.psa.gov.ph/content/highlights-philippine-population-2015-census-population]. It is the 8th most populated country in Asia, and 12th most populated country in the world [https://en.wikipedia.org/wiki/List_of_countries_and_dependencies_by_population]. It is also an emerging economy - currently it is the 36th largest economy by GDP in the world [https://en.wikipedia.org/wiki/List_of_countries_by_GDP_(nominal)] and is projected to grow to be the 20th largest by 2050 [http://www.goldmansachs.com/our-thinking/archive/archive-pdfs/brics-book/brics-chap-13.pdf].

Metro Manila is the most densely populated metropolitan area in the Philippines, and the 5th most densely populated in the world [https://en.wikipedia.org/wiki/List_of_largest_cities]. It also accounts for 37.5% of the Philippine GDP [https://en.wikipedia.org/wiki/Economy_of_the_Philippines].

As an economy grows and the population get more spending power, so will the need for non-essential goods and services. For this reason, I would like to look at the best place to setup gym/recreation area in Metro Manila - mainly because it accounts for a large part of the economy, and there is good access to a large population. With this, we can now determine our problem statement:

## Problem

**Which area should I set up a new gym/recreation area in Metro Manila?**

For the scope of this capstone, we need to look at two things:

1. **Size of potential market**

    - Having a large potential customer base would be a big factor in starting a business. We can determine this by picking districts from the cities with the largest per capita income. We will be looking at this in combination with population density.

    
2. **Competitors in the area**

    - Having competitors in the area is also a big factor. Putting a business where there are no competing establishments would benefit us positively. We will determine this by getting data on nearby venues in foursquare, and by checking the venue types related to gyms and recreation.

## Data sources

To do this analysis, we will need to get raw data from a few places:

- the list of cities in Metro Manila: https://en.wikipedia.org/wiki/Metro_Manila
- population densities for the respective cities
- income per capita in Metro Manila: https://psa.gov.ph/sites/default/files/attachments/hsd/article/Table%202%20AVERAGE%20PER%20CAPITA%20INCOME%20AND%20AVERAGE%20PER%20CAPITA%20EXPENDITURE.pdf
- districts in the target cities in Metro Manila: https://en.wikipedia.org/wiki/List_of_ZIP_codes_in_the_Philippines
- the list of gym/recreation venues in selected districts via foursquare

## Methodology

### Cities in Metro Manila

The metropolitan Manila area is made up of several cities, each with their own districts. To get the list of cities, we will use the Wikipedia page for Metro Manila, which has the latest data from the Philippines' National Statistical Coordination Board.

In [1]:
import numpy as np
import pandas as pd
import requests

metro_manila_page_tables = pd.read_html("https://en.wikipedia.org/wiki/Metro_Manila", header=0)

The cities table is the fifth table in the Wikipedia page:

In [2]:
cities_table = metro_manila_page_tables[5]
cities_table.rename(
    columns={
        'City ormunicipality': 'City',
        'Population (2015)[3]': 'DROPColumn',
        'Population (2015)[3].1': 'Population',
        'Area[a]': 'AreaKM',
        'Area[a].1': 'AreaMi',
        'Density': 'DensityKM',
        'Density.1': 'DensityMi',
        'Incorporated (city)': 'Incorporated',
    }, inplace=True)
cities_table = cities_table.drop(cities_table.loc[cities_table['City'] == 'Pateros'].index) # Pateros is not a city, we'll consider it part of Taguig
cities_table = cities_table.drop(0) # drop duplicate header row in the wiki
cities_table = cities_table.drop(18) # drop the Total row
cities_table = cities_table.drop(19) # drop the annotations row
cities_table.loc[cities_table['City'] == "† City of Manila", ['City']] = 'Manila' # Let's call the City of Manila just Manila for easy joining with the other tables
cities_table = cities_table[['City', 'Population', 'AreaKM']].astype({ 'Population': float, 'AreaKM': float })
cities_table.set_index("City", inplace=True)
cities_table

Population  AreaKM
City                           
Caloocan      1583978.0   53.33
Las Piñas      588894.0   32.02
Makati         582602.0   27.36
Malabon        365525.0   15.96
Mandaluyong    386276.0   11.06
Manila        1780148.0   42.88
Marikina       450741.0   22.64
Muntinlupa     504509.0   41.67
Navotas        249463.0   11.51
Parañaque      664822.0   47.28
Pasay          416522.0   18.64
Pasig          755300.0   31.46
Quezon City   2936116.0  165.33
San Juan       122180.0    5.87
Taguig         804915.0   45.18
Valenzuela     620422.0   45.75

### Population density

We do not have population density by district available in the National Statistics Office database. What we do have is the density by city. We can use this data to calculate the density per area, and use it in the decision making process for picking which district to set up our business.

The table in Wikipedia already has population density per KM, but it is rounded up, so we will calculate it using the population data and land areas instead.

In [3]:
cities_table['Density'] = cities_table['Population'] / cities_table['AreaKM']
cities_table.sort_values('Density', ascending=False, inplace=True)
cities_table

Population  AreaKM       Density
City                                         
Manila        1780148.0   42.88  41514.645522
Mandaluyong    386276.0   11.06  34925.497288
Caloocan      1583978.0   53.33  29701.443840
Pasig          755300.0   31.46  24008.264463
Malabon        365525.0   15.96  22902.568922
Pasay          416522.0   18.64  22345.600858
Navotas        249463.0   11.51  21673.588184
Makati         582602.0   27.36  21293.932749
San Juan       122180.0    5.87  20814.310051
Marikina       450741.0   22.64  19909.054770
Las Piñas      588894.0   32.02  18391.442848
Taguig         804915.0   45.18  17815.737052
Quezon City   2936116.0  165.33  17759.124176
Parañaque      664822.0   47.28  14061.379019
Valenzuela     620422.0   45.75  13561.136612
Muntinlupa     504509.0   41.67  12107.247420

### Per capita income

We use the latest data for per capita income with city breakdowns from the Philippine Statistics Agency and associate the data with the cities in our table.

In [4]:
# The data is in the form of a PDF, so we use tabula-py's read_pdf function
# The data we need is in page 1 of the document
from tabula import read_pdf
metro_manila_per_capita_report_tables = read_pdf("https://psa.gov.ph/sites/default/files/attachments/hsd/article/Table 2 AVERAGE PER CAPITA INCOME AND AVERAGE PER CAPITA EXPENDITURE.pdf", pages=1)

In [5]:
per_capita_table = metro_manila_per_capita_report_tables[0]
per_capita_table.rename(
    columns={
        'PHILIPPINES': 'City',
        '32,141': 'PerCapitaIncome'
    }, inplace=True)
per_capita_table['City'] = per_capita_table['City'].str.title() # Let's convert City names to camel case for easy joining

# Fix some city names to reflect the latest names based on PSA data
per_capita_table.loc[per_capita_table['City'] == "Paranaque", ['City']] = 'Parañaque'
per_capita_table.loc[per_capita_table['City'] == "Las Pinas", ['City']] = 'Las Piñas'
per_capita_table.loc[per_capita_table['City'] == "Caloocan City", ['City']] = 'Caloocan'
per_capita_table.loc[per_capita_table['City'] == "Pasay City", ['City']] = 'Pasay'
per_capita_table.loc[per_capita_table['City'] == "Pateros And Taguig", ['City']] = 'Taguig'
per_capita_table['PerCapitaIncome'] = per_capita_table['PerCapitaIncome'].str.replace(',', '').astype(float)
per_capita_table = per_capita_table[['City', 'PerCapitaIncome']]
per_capita_table.set_index('City', inplace=True)

# We'll join the per capita information with the cities table to see the per capita data just for Metro Manila.
cities_table = cities_table.join(per_capita_table, on="City")

We want a city with high per capita (population with buying power), but also with a good population size. We cannot just pick the places with high per capita income, because they might not have enough people. We'll make this decision by sorting the data based on per capita income, and density of population.

In [6]:
cities_table.sort_values(['PerCapitaIncome', 'Density'], ascending=[False, False], inplace=True)
cities_table

Population  AreaKM       Density  PerCapitaIncome
City                                                          
Makati         582602.0   27.36  21293.932749         140275.0
San Juan       122180.0    5.87  20814.310051         103855.0
Las Piñas      588894.0   32.02  18391.442848          93172.0
Quezon City   2936116.0  165.33  17759.124176          75465.0
Parañaque      664822.0   47.28  14061.379019          75207.0
Pasig          755300.0   31.46  24008.264463          73961.0
Mandaluyong    386276.0   11.06  34925.497288          67143.0
Manila        1780148.0   42.88  41514.645522          60687.0
Pasay          416522.0   18.64  22345.600858          57212.0
Muntinlupa     504509.0   41.67  12107.247420          57121.0
Caloocan      1583978.0   53.33  29701.443840          52855.0
Taguig         804915.0   45.18  17815.737052          52528.0
Marikina       450741.0   22.64  19909.054770          51198.0
Malabon        365525.0   15.96  22902.568922          50720.0
Valenzuela     620422.0   45.75  13561.136612          46603.0
Navotas        249463.0   11.51  21673.588184          31431.0

Looking at the list, it seems Makati is a city with a good per capita income and population. San Juan comes in second, but there is a difference of almost 40,000PHP per capita. Las Piñas is also a good candidate, even if the difference in per capita with Makati is almost 50,000PHP.

Quezon City comes in at 4th and has good per capita income of 75,000PHP but the difference with Makati is almost double per capita. It is also spread across a large area (165 square kilometers).

Because of this, we will pick Makati, San Juan, and Las Piñas districts for our business.

To get the candidate districts in these cities, we will use the list of ZIP codes in the Philippines, and join it with our cities table.

In [7]:
metro_manila_zip_codes = pd.read_html("https://en.wikipedia.org/wiki/List_of_ZIP_codes_in_the_Philippines", header=0)[3]

In [8]:
metro_manila_zip_codes.rename(
    columns={
        'Area': 'Area',
        'Province or city': 'City',
        'ZIP Code': 'ZIPCode'
    }, inplace=True)
metro_manila_zip_codes = metro_manila_zip_codes[['City', 'Area', 'ZIPCode']].astype({ 'ZIPCode': int })
# Get only the cities we need
metro_manila_zip_codes = metro_manila_zip_codes[(metro_manila_zip_codes['City'] == 'Makati') | (metro_manila_zip_codes['City'] == 'San Juan') | (metro_manila_zip_codes['City'] == 'Las Piñas')]
metro_manila_zip_codes.set_index('City', inplace=True)
# Join this with the per capita table
areas_table = metro_manila_zip_codes.join(cities_table, on="City").astype({ 'PerCapitaIncome': str })
areas_table = areas_table[areas_table['PerCapitaIncome'] != "nan"].astype({ 'PerCapitaIncome': float })
areas_table

Area  ZIPCode  Population  AreaKM  \
City                                                                          
San Juan   International Correspondence School      400    122180.0    5.87   
San Juan                Asian Development Bank      401    122180.0    5.87   
San Juan                     Radio Bible Class      410    122180.0    5.87   
San Juan               Bible School on the Air      420    122180.0    5.87   
Makati                  Plain Truth Ministries      700    582602.0   27.36   
...                                        ...      ...         ...     ...   
Las Piñas               Manila Doctors Village     1748    588894.0   32.02   
Las Piñas                       Angela Village     1749    588894.0   32.02   
Las Piñas                              Almanza     1750    588894.0   32.02   
Las Piñas                T.S. Cruz Subdivision     1751    588894.0   32.02   
Las Piñas           Soldiers Hills Subdivision     1752    588894.0   32.02   

                Density  PerCapitaIncome  
City                                      
San Juan   20814.310051         103855.0  
San Juan   20814.310051         103855.0  
San Juan   20814.310051         103855.0  
San Juan   20814.310051         103855.0  
Makati     21293.932749         140275.0  
...                 ...              ...  
Las Piñas  18391.442848          93172.0  
Las Piñas  18391.442848          93172.0  
Las Piñas  18391.442848          93172.0  
Las Piñas  18391.442848          93172.0  
Las Piñas  18391.442848          93172.0  

[96 rows x 6 columns]

## Getting the location data for the selected areas

Next we need to get the latitudes and longitudes of the selected areas using `geocoder`

In [33]:
import geocoder

def geocode_func(postal_code, area, city):
    query = '{}, {}, Metro Manila'.format(area, city)
    print(query)
    g = geocoder.arcgis(query)
    return g.latlng

import time # for sleeps between requests

latitudes = []
longitudes = []

for index, area in areas_table.iterrows():
    location = geocode_func(area["ZIPCode"], area["Area"], index)
    latitudes.append(location[0])
    longitudes.append(location[1])
    time.sleep(1) # add sleep per request to avoid rejected requests
    
areas_table['Latitude'] = latitudes
areas_table['Longitude'] = longitudes
areas_table

International Correspondence School, San Juan, Metro Manila
Asian Development Bank, San Juan, Metro Manila
Radio Bible Class, San Juan, Metro Manila
Bible School on the Air, San Juan, Metro Manila
Plain Truth Ministries, Makati, Metro Manila
Colgate Palmolive Philippines, Makati, Metro Manila
Citibank, Makati, Metro Manila
Sarmiento Enterprises, Makati, Metro Manila
Producers Bank, Makati, Metro Manila
Union Ajinomoto, Makati, Metro Manila
Faith Embassy, Makati, Metro Manila
Canadian Embassy, Makati, Metro Manila
Philippine National Oil Company, Makati, Metro Manila
A-Z Direct Marketing, Makati, Metro Manila
American Express, Makati, Metro Manila
Land Bank of the Philippines, Makati, Metro Manila
Prudential Bank, Makati, Metro Manila
BPI Family Savings Bank, Makati, Metro Manila
Philippine Manila Mission, Makati, Metro Manila
Marcopper Mining Corporation, Makati, Metro Manila
Diners Club, Makati, Metro Manila
International Center for Aquatic Resources, Makati, Metro Manila
Security Ban

Area  ZIPCode  Population  AreaKM  \
City                                                                          
San Juan   International Correspondence School      400    122180.0    5.87   
San Juan                Asian Development Bank      401    122180.0    5.87   
San Juan                     Radio Bible Class      410    122180.0    5.87   
San Juan               Bible School on the Air      420    122180.0    5.87   
Makati                  Plain Truth Ministries      700    582602.0   27.36   
...                                        ...      ...         ...     ...   
Las Piñas               Manila Doctors Village     1748    588894.0   32.02   
Las Piñas                       Angela Village     1749    588894.0   32.02   
Las Piñas                              Almanza     1750    588894.0   32.02   
Las Piñas                T.S. Cruz Subdivision     1751    588894.0   32.02   
Las Piñas           Soldiers Hills Subdivision     1752    588894.0   32.02   

                Density  PerCapitaIncome  Latitude  Longitude  
City                                                           
San Juan   20814.310051         103855.0  -1.28729   36.82838  
San Juan   20814.310051         103855.0  14.58779  121.05964  
San Juan   20814.310051         103855.0  14.60473  121.02904  
San Juan   20814.310051         103855.0  14.60473  121.02904  
Makati     21293.932749         140275.0  14.56872  121.02820  
...                 ...              ...       ...        ...  
Las Piñas  18391.442848          93172.0  14.43799  121.01414  
Las Piñas  18391.442848          93172.0  14.43990  121.00105  
Las Piñas  18391.442848          93172.0  14.44907  120.98255  
Las Piñas  18391.442848          93172.0  14.42864  121.01724  
Las Piñas  18391.442848          93172.0  14.41309  120.99573  

[96 rows x 8 columns]

Let's map the data to verify the locations. Let's use Makati as the map center since most of the venues are there.

In [43]:
import folium

address = "Makati, Metro Manila"
map_location = geolocator.geocode(address)

map_manila = folium.Map(location=[map_location.latitude, map_location.longitude], zoom_start=11)
for lat, lng, area in zip(areas_table['Latitude'], areas_table['Longitude'], areas_table['Area']):
    label = area
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manila)  
    
map_manila

We have a few outliers from bad data. We'll manually clean this areas since we are mostly interested in area coverage, have enough coverage to do the foursquare query even without the outliers.

In [44]:
# Remove these areas from the table:
# International Correspondence School (bad data)
# Zuellig Pharma (it's in Taguig but ARCGis has bad data)
# Equitable PCI Bank (bad data in ARCGis, shows up in Manila)
# Atlantic, Gulf and Pacific (bad data in ARCGis, shows up in Paranaque)
# Producers Bank (bad data in ARCGis, shows up in Caloocan)
# Export and Industry Bank (bad data in ARCGis, shows up in Caloocan)
areas_table = areas_table[
    (areas_table['Area'] != "International Correspondence School") &
    (areas_table['Area'] != "Zuellig Pharma") &
    (areas_table['Area'] != "Equitable PCI Bank") &
    (areas_table['Area'] != "Atlantic, Gulf and Pacific") &
    (areas_table['Area'] != "Producers Bank") &
    (areas_table['Area'] != "Export and Industry Bank")
]

Let's map the locations again to verify coverage:

In [45]:
map_manila = folium.Map(location=[map_location.latitude, map_location.longitude], zoom_start=11)
for lat, lng, area in zip(areas_table['Latitude'], areas_table['Longitude'], areas_table['Area']):
    label = area
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manila)  
    
map_manila

## Getting the venues in the selected areas using Foursquare API

Next we will need to get the list of venues for all of the areas in the selected city using foursquare data.

In [48]:
CLIENT_ID = 'REDACTED' # your Foursquare ID
CLIENT_SECRET = 'REDACTED' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Area', 
                  'Area Latitude', 
                  'Area Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

metro_manila_venues = getNearbyVenues(names=areas_table['Area'],
                                      latitudes=areas_table['Latitude'],
                                      longitudes=areas_table['Longitude'])

Asian Development Bank
Radio Bible Class
Bible School on the Air
Plain Truth Ministries
Colgate Palmolive Philippines
Citibank
Sarmiento Enterprises
Union Ajinomoto
Faith Embassy
Canadian Embassy
Philippine National Oil Company
A-Z Direct Marketing
American Express
Land Bank of the Philippines
Prudential Bank
BPI Family Savings Bank
Philippine Manila Mission
Marcopper Mining Corporation
Diners Club
International Center for Aquatic Resources
Security Bank
Bank of the Philippine Islands
Philippine Long Distance Telephone Company
World Executive Digest
Japanese Embassy
Sun Life Financial
Insular Life Assurance Company
Rizal Commercial Banking Corporation
United Coconut Planters Bank
BCD Direct Marketing
Sycip, Gorres, Velayo and Co.
Philippine Airlines
Pilipinas Shell
ACCRA Law Offices
Mead Johnson Philippines
Directories Philippines Corporation
Makati Central Post Office
Fort Bonifacio
Fort Bonifacio Naval Station
San Antonio Village
La Paz, Singkamas, and Tejeros
Santa Cruz
Kasilawan
Ca

In [49]:
metro_manila_venues

Area  Area Latitude  Area Longitude  \
0         Asian Development Bank       14.58779       121.05964   
1         Asian Development Bank       14.58779       121.05964   
2         Asian Development Bank       14.58779       121.05964   
3         Asian Development Bank       14.58779       121.05964   
4         Asian Development Bank       14.58779       121.05964   
...                          ...            ...             ...   
3432       T.S. Cruz Subdivision       14.42864       121.01724   
3433  Soldiers Hills Subdivision       14.41309       120.99573   
3434  Soldiers Hills Subdivision       14.41309       120.99573   
3435  Soldiers Hills Subdivision       14.41309       120.99573   
3436  Soldiers Hills Subdivision       14.41309       120.99573   

                                  Venue  Venue Latitude  Venue Longitude  \
0                       Polecats Manila       14.586639       121.061063   
1         Toby's Estate Coffee Roasters       14.587986       121.061060   
2               Gino's Brick Oven Pizza       14.585791       121.059640   
3                            Beauty Bar       14.585759       121.059815   
4               Wildflour Café + Bakery       14.585866       121.059573   
...                                 ...             ...              ...   
3432    Pound for Pound Fitness Alabang       14.430207       121.021351   
3433  Soldiers Hills 2 Basketball Court       14.412149       120.995645   
3434          Soldiers hills 2 pathwalk       14.412087       120.997801   
3435              SM Savemore M.Alvarez       14.413140       120.998647   
3436      Potato Corner @ Festival Mall       14.416472       120.994239   

            Venue Category  
0     Gym / Fitness Center  
1              Coffee Shop  
2              Pizza Place  
3           Cosmetics Shop  
4                     Café  
...                    ...  
3432                   Gym  
3433      Basketball Court  
3434    Athletics & Sports  
3435                Market  
3436           Snack Place  

[3437 rows x 7 columns]

Let's map the venues to verify the data

In [52]:
map_manila_venues = folium.Map(location=[map_location.latitude, map_location.longitude], zoom_start=11)
for lat, lng, venue_name in zip(metro_manila_venues['Venue Latitude'], metro_manila_venues['Venue Longitude'], metro_manila_venues['Venue']):
    label = venue_name
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manila_venues)  
    
map_manila_venues

Now we have the data that we need to do our analysis